## Ansible Configuration Management


<style type="text/css">
    /* 1. Style header/footer <div> so they are positioned as desired. */
    #header-left {
        position: absolute;
        top: 2.5%;
        left: 2.5%;
    }
    #header-right {
        position: absolute;
        top: 2.5%;
        right: 2.5%;
    }
    
    #footer-left {
        position: absolute;
        bottom: 2.5%;
        left: 2.5%;
    }
    
    #footer-right {
        position: absolute;
        bottom: 2.5%;
        right: 2.5%;
    }
    
</style>

<!-- 2. Create hidden header/footer <div> -->
<div id="hidden" style="display:none;">
    <div id="header">
        <div id="header-left"><font size=1 color='D33513'> <i>May 2 2023:   <b>Configuration management</b></i></font> </div>
        <div id="header-right"><img src="LCI_logo.png" width="180"></div>
    </div>
</div>

<script src="https://code.jquery.com/jquery-2.2.4.min.js"></script>
<script type="text/javascript">
    // 3. On Reveal.js ready event, copy header/footer <div> into each `.slide-background` <div>
    var header = $('#header').html();
    if ( window.location.search.match( /print-pdf/gi ) ) {
        Reveal.addEventListener( 'ready', function( event ) {
            $('.slide-background').append(header);
        });
    }
    else {
        $('div.reveal').append(header);
   }
</script>



### Outline of the topic:

<br>


- Major server installation types and configuration management challenges
- Detail what configuration management is and why it is useful
- Review the current landscape of available tools
- Ansible basics and examples:
  - configuration files
  - playbooks
  - commands for remote tasks


### Major automated installation types and management challenges

Traditional diskful ("stateful") compute  nodes

![](img/Diskful2.png)

- The operating system and applications reside on the local system drive.
- They are preserved at system reboot.
- Configuration management challenge: 
   - keeping the OS and apps identical across the cluster nodes.
- Configuration tools: <b>ansible, puppet, chef, salt, cfengine</b>.


### Defining Configuration Management

<br>

At its broadest level, the management and maintenance of operating system and service configuration via code instead of manual intervention.

More formally:
- Declaring the system state in a repeatable and auditable fashion and using tools to impose state and prevent systems from deviating



### State

<br>

All system have a ‘state’ comprised of:
- Files on Disk
- Running services

State can be supplied by:
- Installation / provisioning systems
- Golden Images
- Manual steps including direct configuration changes and setup scripts



### Modern Configuration Management Features

<br>

- Idempotency
  - Declaration and management of files and services to reach a ‘desired state’
- Revision Control
  - Systems are managed with an ‘Infrastructure as code’ model
- Composable and flexible


### Benefits of configuration management

<br>

- Centralized catalog of all system configuration
- Automated enforcement of system state from an authoritative source
- Ensured consistency between systems
- Rapid system provisioning from easily-composed components
- Preflight tests to ensure deployments generate expected results
- Collection of system ‘ground truths’ for better decision making


### Modern configuration-management systems

<br>

- Puppet
  - Ruby based 
- Chef Infra
  - Ruby based
- CFEngine
  - C based
- Salt
  - Python based
- <b>Ansible</b>
  - Python based



### How Ansible works

<br>

- Ansible connects to compute nodes via ```ssh``` as a regular user.
  - Needs either public-private key for the user running ansible, or host based authentication configured.
- Forks several instances to ssh concurrently to multiple nodes.
- Elevates root privileges via ```sudo```.
  - Needs sudo privilege on the nodes for a user running ansible.
- Runs configuration/management tasks via ```python``` modules.
  - Needs python3 as well as Ansible python modules (ansible-core) installed.
- The tasks are defined in Ansible ```playbooks``` (yaml files).
  - The admin needs to understand yaml syntax for ansible tasks. 
- Doesn't touch the system and configuration if they are already in the desired final target state.

### A simple Ansible setup example

<br>

- Ansible file structure for host name change on the nodes. All the files are under:
<br>

```c
Ansible/
        |-- ansible.cfg
        |-- hosts.ini
        |-- fix_hostname_tasks.yml
        \-- files

```

### The main config file,  `ansible.cfg` on our cluster

<br><br>

```yaml
[defaults]
inventory = hosts.ini
remote_user = hostadm
host_key_checking = false
remote_tmp = /tmp/.ansible/tmp
interpreter_python = /bin/python3
forks = 1

[privilege_escalation]
become = true
become_method = sudo
become_user = root
become_ack_pass = false
```

### Inventory (hosts) file ```hosts.ini```

<br><br>

```c
[ceph_nodes]
node03

```

### Playbook ```fix_hostname_tasks.yml ```


<br>

- The file can have any name. 
- The extension is ```.yaml```. 
- The configuration syntax is Yaml.
- All the work is done by the ```tasks```:


```yaml
---
- name: fix hostname
  hosts: ceph_nodes

  tasks:

    - name: fix the hostname
      ansible.builtin.hostname:
        name: "{{ inventory_hostname }}"

    - name: fix hosts file
      ansible.builtin.copy:
        src: hosts
        dest: /etc/hosts
```

### Ansible organization: playbook, play, role, and task.

<br><br>

- Plays are associated with groups of hosts in the inventory.
- Roles contain collections of reusable tasks.
- Tasks perform all the work by utilizing modules.


![](img/Ansible_play.png)

### Ansible modules
<br>

- The modules are used by tasks to do work.
- The most commonly used modules:
    - copy files: ```ansible.builtin.copy```
    - set file attributes: ```ansible.builtin.file```
    - install packages: ```ansible.builtin.dnf``` and ```ansible.builtin.apt```
    - execute shell commands: ```ansible.builtin.shell```
    - restart a service: ```ansible.builtin.service```
    - modify a config file: ```ansible.builtin.lineinfile```
    
    To see all installed on your system modules:
    ```bash
    ansible-doc -l
    ```
    Read the info on a specific module, for example, ```ansible.builtin.file```:
    ```bash
    ansible-doc   ansible.builtin.file
    ```

### Examples of utilizing ```ansible.builtin.shell``` module for a remote command

<br><br>

- Use module ```ansible.builtin.shell``` for a remote command.

- For example, check the status of ```sshd``` on all the nodes:

```bash

ansible all -m ansible.builtin.shell -a "systemctl status sshd"
```


- Restart ```slurmd``` on compute1:


```bash
ansible compute1 -m ansible.builtin.shell -a "systemctl restart sshd"
```

### Ansible playbook development steps

<br><br>

- Set Configuration files: ```ansible.cfg``` and ```hosts.ini```.
- Identify groups of hosts to execute identical tasks on (plays)
- Define the top-level playbook tasks (roles).
- Add features you need in new yaml files.
- Place configuration files and packages in the ``files`` directories for the roles.
- Define variables (parameters) and put them in a variables file.
- Tag the tasks for debugging purposes.
- Check the playbooks for syntactic errors:
```bash
ansible-playbook playbook.yml --syntax-check
```
- Perform a dry run:
```bash
ansible-playbook playbook.yml --check
```
- List the tagged tasks:
```
ansible-playbook --list-tags playbook.yml
```
- Run only the tagged task in the playbook with tag ```OSD```, for example: 
```bash
ansible-playbook --tags OSD playbook.yml
```
- Run the playbook:
```bash
ansible-playbook playbook.yml
```

### References

[Ansible documentation and HOWTOs](https://docs.ansible.com/ansible/latest/)

### Questions and discussion: